In [ ]:
import nltk
nltk.download('gutenberg')

[nltk_data] Downloading package gutenberg to /root/nltk_data...
[nltk_data]   Unzipping corpora/gutenberg.zip.


True

In [ ]:
from nltk.corpus import gutenberg

In [ ]:
filenames = gutenberg.fileids()

In [ ]:
def text_to_words(inp_text):
  out_text = re.sub('[^A-Za-z]+', ' ', inp_text) # remove non-alphabets
  out_text = re.sub(r'(?:^| )\w(?:$| )', ' ', out_text).strip() # remove single letter words
  out_text = out_text.lower() # make all characters lower-case
  words = out_text.split() # tokenise
  filtered_words = []
  for word in words:
    if word not in stopWords: # discard stop words
      filtered_words.append(word)
  return filtered_words

In [ ]:
nltk.download('stopwords')
from nltk.corpus import stopwords

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [ ]:
stopWords = set(stopwords.words('english'))

In [ ]:
import json
with open('/content/drive/MyDrive/CS772/scraped_sentences.txt', 'r') as f:
    data = json.load(f)

In [10]:
import re
vocab = []
tw_map = []
for file in filenames:
  word_list = gutenberg.words(file)
  text = ' '.join(word_list)
  words = text_to_words(text)
  vocab += words
  tw_map.append(words)
len(vocab), len(tw_map)

(1025404, 18)

In [11]:
topic_sents = list(data.values())
for sents in topic_sents:
  text = ' '.join(sents)
  words = text_to_words(text)
  vocab += words
  tw_map.append(words)
len(vocab), len(tw_map)

(3814529, 164)

In [12]:
from collections import Counter
count_map = Counter(vocab)
len(count_map)

96393

In [13]:
new_vocab = []
for key, val in count_map.items():
  if val>5:
    new_vocab.append(key)
len(new_vocab)

35243

In [14]:
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
LE = LabelEncoder()
labels = LE.fit_transform(new_vocab)
labels = labels.reshape(len(labels),1)
OE = OneHotEncoder(sparse=False)
OE.fit(labels)

OneHotEncoder(sparse=False)

In [ ]:
len(tw_map[0])

73261

In [ ]:
vocab_set = set(new_vocab)
new_tw_map = [[word for word in wtype if word in vocab_set] for wtype in tw_map]
len(new_tw_map)

164

In [ ]:
len(new_tw_map[0])

72030

In [ ]:
word_data = []
for wtype in new_tw_map:
  for i in range(2,len(wtype)-2):
    window = [wtype[i-2],wtype[i-1],wtype[i+1],wtype[i+2],wtype[i]]
    word_data.append(window)
np.array(word_data).shape

(3676534, 5)

In [ ]:
import numpy as np
import torch
from torch.utils.data import Dataset, DataLoader

In [ ]:
class CustomDataset(Dataset):
    def __init__(self):
        self.data = np.array(word_data)
    def __len__(self):
        return len(self.data)
    def __getitem__(self, idx):
        window = self.data[idx]
        wlabels = LE.transform(window)
        wlabels = wlabels.reshape(len(wlabels),1)
        wvectors = OE.transform(wlabels)
        wtensors = torch.from_numpy(wvectors)        
        return wtensors[:-1], wtensors[-1]

In [ ]:
dataset = CustomDataset()
data_loader = DataLoader(dataset, batch_size=3, shuffle=True)

In [ ]:
for (idx, batch) in enumerate(data_loader):
  print(idx,batch)
  if idx==5:
    break

0 [tensor([[[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]]], dtype=torch.float64), tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]], dtype=torch.float64)]
1 [tensor([[[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]],


###Trials

In [ ]:
gutenberg.fileids()

['austen-emma.txt',
 'austen-persuasion.txt',
 'austen-sense.txt',
 'bible-kjv.txt',
 'blake-poems.txt',
 'bryant-stories.txt',
 'burgess-busterbrown.txt',
 'carroll-alice.txt',
 'chesterton-ball.txt',
 'chesterton-brown.txt',
 'chesterton-thursday.txt',
 'edgeworth-parents.txt',
 'melville-moby_dick.txt',
 'milton-paradise.txt',
 'shakespeare-caesar.txt',
 'shakespeare-hamlet.txt',
 'shakespeare-macbeth.txt',
 'whitman-leaves.txt']

In [ ]:
g1 = gutenberg.words('austen-emma.txt')
g1, len(g1)

(['[', 'Emma', 'by', 'Jane', 'Austen', '1816', ']', ...], 192427)

In [ ]:
text_data = ' '.join(g1)
text_data

'[ Emma by Jane Austen 1816 ] VOLUME I CHAPTER I Emma Woodhouse , handsome , clever , and rich , with a comfortable home and happy disposition , seemed to unite some of the best blessings of existence ; and had lived nearly twenty - one years in the world with very little to distress or vex her . She was the youngest of the two daughters of a most affectionate , indulgent father ; and had , in consequence of her sister \' s marriage , been mistress of his house from a very early period . Her mother had died too long ago for her to have more than an indistinct remembrance of her caresses ; and her place had been supplied by an excellent woman as governess , who had fallen little short of a mother in affection . Sixteen years had Miss Taylor been in Mr . Woodhouse \' s family , less as a governess than a friend , very fond of both daughters , but particularly of Emma . Between _them_ it was more the intimacy of sisters . Even before Miss Taylor had ceased to hold the nominal office of go

In [ ]:
import re
text_data_2 = re.sub('[^A-Za-z]+', ' ', text_data)
text_data_2

' Emma by Jane Austen VOLUME I CHAPTER I Emma Woodhouse handsome clever and rich with a comfortable home and happy disposition seemed to unite some of the best blessings of existence and had lived nearly twenty one years in the world with very little to distress or vex her She was the youngest of the two daughters of a most affectionate indulgent father and had in consequence of her sister s marriage been mistress of his house from a very early period Her mother had died too long ago for her to have more than an indistinct remembrance of her caresses and her place had been supplied by an excellent woman as governess who had fallen little short of a mother in affection Sixteen years had Miss Taylor been in Mr Woodhouse s family less as a governess than a friend very fond of both daughters but particularly of Emma Between them it was more the intimacy of sisters Even before Miss Taylor had ceased to hold the nominal office of governess the mildness of her temper had hardly allowed her to

In [ ]:
text_data_3 = text_data_2.lower()
text_data_3

' emma by jane austen volume i chapter i emma woodhouse handsome clever and rich with a comfortable home and happy disposition seemed to unite some of the best blessings of existence and had lived nearly twenty one years in the world with very little to distress or vex her she was the youngest of the two daughters of a most affectionate indulgent father and had in consequence of her sister s marriage been mistress of his house from a very early period her mother had died too long ago for her to have more than an indistinct remembrance of her caresses and her place had been supplied by an excellent woman as governess who had fallen little short of a mother in affection sixteen years had miss taylor been in mr woodhouse s family less as a governess than a friend very fond of both daughters but particularly of emma between them it was more the intimacy of sisters even before miss taylor had ceased to hold the nominal office of governess the mildness of her temper had hardly allowed her to

In [ ]:
text_data_4 = re.sub(r'(?:^| )\w(?:$| )', ' ', text_data_3).strip()
text_data_4

'emma by jane austen volume chapter emma woodhouse handsome clever and rich with comfortable home and happy disposition seemed to unite some of the best blessings of existence and had lived nearly twenty one years in the world with very little to distress or vex her she was the youngest of the two daughters of most affectionate indulgent father and had in consequence of her sister marriage been mistress of his house from very early period her mother had died too long ago for her to have more than an indistinct remembrance of her caresses and her place had been supplied by an excellent woman as governess who had fallen little short of mother in affection sixteen years had miss taylor been in mr woodhouse family less as governess than friend very fond of both daughters but particularly of emma between them it was more the intimacy of sisters even before miss taylor had ceased to hold the nominal office of governess the mildness of her temper had hardly allowed her to impose any restraint

In [ ]:
td5 = text_data_4.split()
td5

['emma',
 'by',
 'jane',
 'austen',
 'volume',
 'chapter',
 'emma',
 'woodhouse',
 'handsome',
 'clever',
 'and',
 'rich',
 'with',
 'comfortable',
 'home',
 'and',
 'happy',
 'disposition',
 'seemed',
 'to',
 'unite',
 'some',
 'of',
 'the',
 'best',
 'blessings',
 'of',
 'existence',
 'and',
 'had',
 'lived',
 'nearly',
 'twenty',
 'one',
 'years',
 'in',
 'the',
 'world',
 'with',
 'very',
 'little',
 'to',
 'distress',
 'or',
 'vex',
 'her',
 'she',
 'was',
 'the',
 'youngest',
 'of',
 'the',
 'two',
 'daughters',
 'of',
 'most',
 'affectionate',
 'indulgent',
 'father',
 'and',
 'had',
 'in',
 'consequence',
 'of',
 'her',
 'sister',
 'marriage',
 'been',
 'mistress',
 'of',
 'his',
 'house',
 'from',
 'very',
 'early',
 'period',
 'her',
 'mother',
 'had',
 'died',
 'too',
 'long',
 'ago',
 'for',
 'her',
 'to',
 'have',
 'more',
 'than',
 'an',
 'indistinct',
 'remembrance',
 'of',
 'her',
 'caresses',
 'and',
 'her',
 'place',
 'had',
 'been',
 'supplied',
 'by',
 'an',
 'excel

In [ ]:
v1 = list(data.values())[0]
v1

['Athens  is a coastal city in the Mediterranean and is both the capital and largest city of Greece.',
 "Athens dominates and is the capital of the Attica region and is one of the world's oldest cities, with its recorded history spanning over 3,400 years and its earliest human presence beginning somewhere between the 11th and 7th millennia BC..",
 'Classical Athens was a powerful city-state.',
 "It was a centre for the arts, learning and philosophy, and the home of Plato's Academy and Aristotle's Lyceum. It is widely referred to as the cradle of Western civilization and the birthplace of democracy, largely because of its cultural and political influence on the European continent—particularly Ancient Rome. In modern times, Athens is a large cosmopolitan metropolis and central to economic, financial, industrial, maritime, political and cultural life in Greece.",
 "In 2021, Athens' urban area hosted more than three and a half million people, which is around 35% of the entire population of

In [ ]:
v2 = ' '.join(v1)
v2

'Athens  is a coastal city in the Mediterranean and is both the capital and largest city of Greece. Athens dominates and is the capital of the Attica region and is one of the world\'s oldest cities, with its recorded history spanning over 3,400 years and its earliest human presence beginning somewhere between the 11th and 7th millennia BC.. Classical Athens was a powerful city-state. It was a centre for the arts, learning and philosophy, and the home of Plato\'s Academy and Aristotle\'s Lyceum. It is widely referred to as the cradle of Western civilization and the birthplace of democracy, largely because of its cultural and political influence on the European continent—particularly Ancient Rome. In modern times, Athens is a large cosmopolitan metropolis and central to economic, financial, industrial, maritime, political and cultural life in Greece. In 2021, Athens\' urban area hosted more than three and a half million people, which is around 35% of the entire population of Greece.. Ath

In [ ]:
v3 = text_to_words(v2)
v3

['athens',
 'coastal',
 'city',
 'mediterranean',
 'capital',
 'largest',
 'city',
 'greece',
 'athens',
 'dominates',
 'capital',
 'attica',
 'region',
 'one',
 'world',
 'oldest',
 'cities',
 'recorded',
 'history',
 'spanning',
 'years',
 'earliest',
 'human',
 'presence',
 'beginning',
 'somewhere',
 'th',
 'th',
 'millennia',
 'bc',
 'classical',
 'athens',
 'powerful',
 'city',
 'state',
 'centre',
 'arts',
 'learning',
 'philosophy',
 'home',
 'plato',
 'academy',
 'aristotle',
 'lyceum',
 'widely',
 'referred',
 'cradle',
 'western',
 'civilization',
 'birthplace',
 'democracy',
 'largely',
 'cultural',
 'political',
 'influence',
 'european',
 'continent',
 'particularly',
 'ancient',
 'rome',
 'modern',
 'times',
 'athens',
 'large',
 'cosmopolitan',
 'metropolis',
 'central',
 'economic',
 'financial',
 'industrial',
 'maritime',
 'political',
 'cultural',
 'life',
 'greece',
 'athens',
 'urban',
 'area',
 'hosted',
 'three',
 'half',
 'million',
 'people',
 'around',
 'enti

In [ ]:
g3 = text_to_words(text_data)
g3

['emma',
 'jane',
 'austen',
 'volume',
 'chapter',
 'emma',
 'woodhouse',
 'handsome',
 'clever',
 'rich',
 'comfortable',
 'home',
 'happy',
 'disposition',
 'seemed',
 'unite',
 'best',
 'blessings',
 'existence',
 'lived',
 'nearly',
 'twenty',
 'one',
 'years',
 'world',
 'little',
 'distress',
 'vex',
 'youngest',
 'two',
 'daughters',
 'affectionate',
 'indulgent',
 'father',
 'consequence',
 'sister',
 'marriage',
 'mistress',
 'house',
 'early',
 'period',
 'mother',
 'died',
 'long',
 'ago',
 'indistinct',
 'remembrance',
 'caresses',
 'place',
 'supplied',
 'excellent',
 'woman',
 'governess',
 'fallen',
 'little',
 'short',
 'mother',
 'affection',
 'sixteen',
 'years',
 'miss',
 'taylor',
 'mr',
 'woodhouse',
 'family',
 'less',
 'governess',
 'friend',
 'fond',
 'daughters',
 'particularly',
 'emma',
 'intimacy',
 'sisters',
 'even',
 'miss',
 'taylor',
 'ceased',
 'hold',
 'nominal',
 'office',
 'governess',
 'mildness',
 'temper',
 'hardly',
 'allowed',
 'impose',
 'res

In [ ]:
len(g3)

73261

In [ ]:
len(v3)

18559

In [ ]:
corp = v3 +g3
len(corp)

91820

In [ ]:
from collections import Counter
lst_cnt = Counter(corp)
lst_cnt

Counter({'athens': 1304,
         'coastal': 12,
         'city': 284,
         'mediterranean': 8,
         'capital': 66,
         'largest': 47,
         'greece': 117,
         'dominates': 2,
         'attica': 42,
         'region': 24,
         'one': 523,
         'world': 124,
         'oldest': 12,
         'cities': 46,
         'recorded': 14,
         'history': 31,
         'spanning': 6,
         'years': 97,
         'earliest': 3,
         'human': 17,
         'presence': 10,
         'beginning': 44,
         'somewhere': 6,
         'th': 78,
         'millennia': 4,
         'bc': 74,
         'classical': 18,
         'powerful': 9,
         'state': 117,
         'centre': 45,
         'arts': 22,
         'learning': 12,
         'philosophy': 14,
         'home': 164,
         'plato': 12,
         'academy': 26,
         'aristotle': 10,
         'lyceum': 4,
         'widely': 7,
         'referred': 16,
         'cradle': 2,
         'western': 39,
         

In [ ]:
len(lst_cnt)

8997

In [ ]:
lst_cnt.items()

dict_items([('athens', 1304), ('coastal', 12), ('city', 284), ('mediterranean', 8), ('capital', 66), ('largest', 47), ('greece', 117), ('dominates', 2), ('attica', 42), ('region', 24), ('one', 523), ('world', 124), ('oldest', 12), ('cities', 46), ('recorded', 14), ('history', 31), ('spanning', 6), ('years', 97), ('earliest', 3), ('human', 17), ('presence', 10), ('beginning', 44), ('somewhere', 6), ('th', 78), ('millennia', 4), ('bc', 74), ('classical', 18), ('powerful', 9), ('state', 117), ('centre', 45), ('arts', 22), ('learning', 12), ('philosophy', 14), ('home', 164), ('plato', 12), ('academy', 26), ('aristotle', 10), ('lyceum', 4), ('widely', 7), ('referred', 16), ('cradle', 2), ('western', 39), ('civilization', 12), ('birthplace', 6), ('democracy', 18), ('largely', 14), ('cultural', 24), ('political', 10), ('influence', 30), ('european', 24), ('continent', 2), ('particularly', 56), ('ancient', 47), ('rome', 6), ('modern', 51), ('times', 39), ('large', 69), ('cosmopolitan', 2), ('m

In [ ]:
new_corp = []
for key, val in lst_cnt.items():
  if val>2:
    new_corp.append(key)
len(new_corp)

4313

In [ ]:
new_corp

['athens',
 'coastal',
 'city',
 'mediterranean',
 'capital',
 'largest',
 'greece',
 'attica',
 'region',
 'one',
 'world',
 'oldest',
 'cities',
 'recorded',
 'history',
 'spanning',
 'years',
 'earliest',
 'human',
 'presence',
 'beginning',
 'somewhere',
 'th',
 'millennia',
 'bc',
 'classical',
 'powerful',
 'state',
 'centre',
 'arts',
 'learning',
 'philosophy',
 'home',
 'plato',
 'academy',
 'aristotle',
 'lyceum',
 'widely',
 'referred',
 'western',
 'civilization',
 'birthplace',
 'democracy',
 'largely',
 'cultural',
 'political',
 'influence',
 'european',
 'particularly',
 'ancient',
 'rome',
 'modern',
 'times',
 'large',
 'metropolis',
 'central',
 'economic',
 'financial',
 'industrial',
 'maritime',
 'life',
 'urban',
 'area',
 'hosted',
 'three',
 'half',
 'million',
 'people',
 'around',
 'entire',
 'population',
 'status',
 'global',
 'according',
 'research',
 'network',
 'biggest',
 'centers',
 'southeastern',
 'europe',
 'municipality',
 'actually',
 'small',
 '

In [ ]:
v4 = []
for word in v3:
  if word in new_corp:
    v4.append(word)
len(v4)

16030

In [22]:
contexts = []
targets = []
for wtype in new_tw_map:
  for i in range(2,len(wtype)-2):
    context = [wtype[i-2],wtype[i-1],wtype[i+1],wtype[i+2]]
    target = wtype[i]
    contexts.append(context)
    targets.append(target)
np.array(contexts).shape, len(targets)

((3676534, 4), 3676534)

In [ ]:
class CustomDataset(Dataset):
    def __init__(self):
        self.ctxts = np.array(contexts)
        self.tgts = np.array(targets)
    def __len__(self):
        return len(self.tgts)
    def __getitem__(self, idx):
        context, target = self.ctxts[idx], self.tgts[idx]
        ctxt_lbl, tgt_lbl = LE.transform(context), LE.transform(target)
        ctxt_lbl, tgt_lbl = ctxt_lbl.reshape(len(ctxt_lbl),1), tgt_lbl.reshape(len(tgt_lbl),1)
        ctxt_vec, tgt_vec = OE.transform(ctxt_lbl), OE.transform(tgt_lbl)
        ctxt_ten, tgt_ten = torch.from_numpy(ctxt_)        
        return img_tensor, class_id

In [26]:
a = torch.tensor([[1,0,0],[0,1,0],[0,0,1]])

In [30]:
a[:-1]

tensor([[1, 0, 0],
        [0, 1, 0]])

In [31]:
a[-1]

tensor([0, 0, 1])

In [ ]:
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
LE = LabelEncoder()
labels = LE.fit_transform(new_corp)
labels = labels.reshape(len(labels),1)
OE = OneHotEncoder(sparse=False)
vectors = OE.fit_transform(labels)
vectors

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [ ]:
vectors.shape

(4313, 4313)

In [ ]:
v41 = LE.transform(v4)
v41 = v41.reshape(len(v41),1)
v42 = OE.transform(v41)
v42

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [ ]:
v42.shape

(16030, 4313)

In [ ]:
word_list = []
stopWords = set(stopwords.words('english'))
for item in td5:
  if item not in stopWords:
    word_list.append(item)

In [ ]:
word_list = []
for item in td5:
  if item not in stopWords:
    word_list.append(item)

In [ ]:
word_list, len(word_list)

(['emma',
  'jane',
  'austen',
  'volume',
  'chapter',
  'emma',
  'woodhouse',
  'handsome',
  'clever',
  'rich',
  'comfortable',
  'home',
  'happy',
  'disposition',
  'seemed',
  'unite',
  'best',
  'blessings',
  'existence',
  'lived',
  'nearly',
  'twenty',
  'one',
  'years',
  'world',
  'little',
  'distress',
  'vex',
  'youngest',
  'two',
  'daughters',
  'affectionate',
  'indulgent',
  'father',
  'consequence',
  'sister',
  'marriage',
  'mistress',
  'house',
  'early',
  'period',
  'mother',
  'died',
  'long',
  'ago',
  'indistinct',
  'remembrance',
  'caresses',
  'place',
  'supplied',
  'excellent',
  'woman',
  'governess',
  'fallen',
  'little',
  'short',
  'mother',
  'affection',
  'sixteen',
  'years',
  'miss',
  'taylor',
  'mr',
  'woodhouse',
  'family',
  'less',
  'governess',
  'friend',
  'fond',
  'daughters',
  'particularly',
  'emma',
  'intimacy',
  'sisters',
  'even',
  'miss',
  'taylor',
  'ceased',
  'hold',
  'nominal',
  'offic